# Watershed challenge

In [1]:
import pandas as pd
from numpy import loadtxt
from xgboost import XGBClassifier
import sklearn
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
import altair as alt
import numpy as np

In [2]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

## 1. Download the file `flux.csv` from github (compressed as `flux.csv.zip`).

In [3]:
df = pd.read_csv('flux.csv')

In [4]:
df.head()

date  basin_id   flux  precip   temp_max                 gauge_name  \
0  1980-01-01   1001001  0.579     0.0  10.685653  Rio Caquena En Nacimiento   
1  1980-01-02   1001001  0.543     0.0  11.470960  Rio Caquena En Nacimiento   
2  1980-01-03   1001001  0.482     0.0  11.947457  Rio Caquena En Nacimiento   
3  1980-01-04   1001001  0.459     0.0  12.424489  Rio Caquena En Nacimiento   
4  1980-01-05   1001001  0.436     0.0  12.649203  Rio Caquena En Nacimiento   

       lat      lon    mean_elev   area_km2  
0 -18.0769 -69.1961  4842.449328  49.711859  
1 -18.0769 -69.1961  4842.449328  49.711859  
2 -18.0769 -69.1961  4842.449328  49.711859  
3 -18.0769 -69.1961  4842.449328  49.711859  
4 -18.0769 -69.1961  4842.449328  49.711859

## 2. Perform an EDA over `flux.csv` file.

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4180480 entries, 0 to 4180479
Data columns (total 10 columns):
 #   Column      Dtype  
---  ------      -----  
 0   date        object 
 1   basin_id    int64  
 2   flux        float64
 3   precip      float64
 4   temp_max    float64
 5   gauge_name  object 
 6   lat         float64
 7   lon         float64
 8   mean_elev   float64
 9   area_km2    float64
dtypes: float64(7), int64(1), object(2)
memory usage: 318.9+ MB


### Checking missing values

In [6]:
df.isna().any()

date          False
basin_id      False
flux          False
precip         True
temp_max       True
gauge_name    False
lat           False
lon           False
mean_elev     False
area_km2      False
dtype: bool

Columns precip and temp_max contains missing values. Let's check it and decide what to do with them.

In [7]:
df[df.precip.isna()]

date  basin_id   flux  precip  temp_max  \
60493    2020-05-06   1021001  1.707     NaN       NaN   
60494    2020-05-07   1021001  1.687     NaN       NaN   
60495    2020-05-08   1021001  1.698     NaN       NaN   
60496    2020-05-09   1021001  1.694     NaN       NaN   
60497    2020-05-10   1021001  1.690     NaN       NaN   
...             ...       ...    ...     ...       ...   
4180475  2020-06-02  12930001  0.375     NaN       NaN   
4180476  2020-06-03  12930001  0.342     NaN       NaN   
4180477  2020-06-04  12930001  0.325     NaN       NaN   
4180478  2020-06-05  12930001  0.311     NaN       NaN   
4180479  2020-06-06  12930001  0.294     NaN       NaN   

                                 gauge_name      lat      lon    mean_elev  \
60493    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60494    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60495    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60496    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60497    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
...                                     ...      ...      ...          ...   
4180475       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180476       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180477       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180478       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180479       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   

            area_km2  
60493    3277.980908  
60494    3277.980908  
60495    3277.980908  
60496    3277.980908  
60497    3277.980908  
...              ...  
4180475    20.645617  
4180476    20.645617  
4180477    20.645617  
4180478    20.645617  
4180479    20.645617  

[5443 rows x 10 columns]

In [8]:
df[df.temp_max.isna()]

date  basin_id   flux  precip  temp_max  \
60493    2020-05-06   1021001  1.707     NaN       NaN   
60494    2020-05-07   1021001  1.687     NaN       NaN   
60495    2020-05-08   1021001  1.698     NaN       NaN   
60496    2020-05-09   1021001  1.694     NaN       NaN   
60497    2020-05-10   1021001  1.690     NaN       NaN   
...             ...       ...    ...     ...       ...   
4180475  2020-06-02  12930001  0.375     NaN       NaN   
4180476  2020-06-03  12930001  0.342     NaN       NaN   
4180477  2020-06-04  12930001  0.325     NaN       NaN   
4180478  2020-06-05  12930001  0.311     NaN       NaN   
4180479  2020-06-06  12930001  0.294     NaN       NaN   

                                 gauge_name      lat      lon    mean_elev  \
60493    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60494    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60495    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60496    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
60497    Rio Lauca En Japu (O En El Limite) -18.5833 -69.0467  4493.855498   
...                                     ...      ...      ...          ...   
4180475       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180476       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180477       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180478       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   
4180479       Rio Robalo En Puerto Williams -54.9469 -67.6392   520.849289   

            area_km2  
60493    3277.980908  
60494    3277.980908  
60495    3277.980908  
60496    3277.980908  
60497    3277.980908  
...              ...  
4180475    20.645617  
4180476    20.645617  
4180477    20.645617  
4180478    20.645617  
4180479    20.645617  

[5443 rows x 10 columns]

Apparently, the rows containing missing values on both columns precip and temp_max are the same. Let's check it.

In [9]:
df[df.temp_max.isna()].index.equals(df[df.precip.isna()].index)

True

Now we confirmed that the same observations didn't registered precip and temp_max, let's calculate how much it represents of the complete database.

In [10]:
len(df[df.precip.isna()])/len(df)

0.0013020035976729946

In [11]:
df[df.precip.isna()].date.value_counts().sort_index()

2020-05-01      4
2020-05-02      4
2020-05-03      4
2020-05-04      4
2020-05-05      4
2020-05-06    171
2020-05-07    172
2020-05-08    172
2020-05-09    172
2020-05-10    173
2020-05-11    172
2020-05-12    172
2020-05-13    173
2020-05-14    173
2020-05-15    173
2020-05-16    172
2020-05-17    173
2020-05-18    172
2020-05-19    172
2020-05-20    171
2020-05-21    168
2020-05-22    169
2020-05-23    169
2020-05-24    170
2020-05-25    170
2020-05-26    169
2020-05-27    169
2020-05-28    167
2020-05-29    168
2020-05-30    166
2020-05-31    165
2020-06-01    166
2020-06-02    165
2020-06-03    165
2020-06-04    164
2020-06-05    165
2020-06-06    165
Name: date, dtype: int64

In [12]:
df[(~df.precip.isna())&(df.date>'2020-05-01')].date.value_counts().sort_index()

Series([], Name: date, dtype: int64)

Only 0.13% of rows contain missing values on columns precip and temp_max and they are concentrated in the last months (May and June 2020) of observation. Considering this quantity irrelevant and that reducing only one month of observation will not represent a great different in our database, we can discart these rows instead of trying to fill it with any input strategy.

In [13]:
df.dropna(axis=0, how='any',inplace=True)

### Observations' distribution over time

In [14]:
df['date'] = pd.to_datetime(df.date)

In [15]:
df.date.describe(datetime_is_numeric=True)

count                          4175037
mean     2001-08-29 15:30:38.407563008
min                1980-01-01 00:00:00
25%                1992-04-05 00:00:00
50%                2002-09-04 00:00:00
75%                2011-05-08 00:00:00
max                2020-04-30 00:00:00
Name: date, dtype: object

In [16]:
idx = pd.date_range('1980-01-01', '2020-04-30')

In [17]:
len(idx)

14731

In [18]:
df.date.nunique()

14731

There are no missing dates in the period observed. So all date in range between min and max date contains observations and we don't need to fill value in number of observations on missing date with 0 to garantee that all dates are being showed in the timeline. 

In [19]:
observations_over_time = df.date.value_counts().reset_index()
observations_over_time.rename(columns={'index':'date', 'date': 'number_of_observations'},inplace=True)

In [20]:
alt.Chart(observations_over_time).mark_line().encode(
    x=alt.X("date"),
    y=alt.Y('number_of_observations')
)

alt.Chart(...)

In [21]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4175037 entries, 0 to 4180447
Data columns (total 10 columns):
 #   Column      Dtype         
---  ------      -----         
 0   date        datetime64[ns]
 1   basin_id    int64         
 2   flux        float64       
 3   precip      float64       
 4   temp_max    float64       
 5   gauge_name  object        
 6   lat         float64       
 7   lon         float64       
 8   mean_elev   float64       
 9   area_km2    float64       
dtypes: datetime64[ns](1), float64(7), int64(1), object(1)
memory usage: 350.4+ MB


### Understanding the relation between basin_id and gauge_name

In [22]:
df.basin_id.nunique()

503

In [23]:
df.gauge_name.nunique()

503

Both columns contains the same number of unique values, so it may indicate that each gauge_name is associated with an unique basin_id. Let's verify it.

In [24]:
df[['basin_id','gauge_name']].drop_duplicates()

basin_id                                   gauge_name
0         1001001                    Rio Caquena En Nacimiento
6125      1001002                     Rio Caquena En Vertedero
18433     1001003              Rio Colpacagua En Desembocadura
27755     1020002                   Rio Desaguadero Cotacotani
39546     1020003                Rio Lauca En Estancia El Lago
...           ...                                          ...
4150797  12872001                  Rio Herminita En Ruta Y-895
4154451  12876001               Rio Grande En Tierra Del Fuego
4167973  12876004               Rio Catalina En Pampa Guanacos
4169448  12878001  Rio Rasmussen En Frontera (Estancia VicuÑA)
4174885  12930001                Rio Robalo En Puerto Williams

[503 rows x 2 columns]

After droping duplicates of a combination of both columns, the number of rows remains the same of the number of basin_id and gauge_name. It means that each basin_id is associate with just one gauge_name. Then, both columns indicate in what station the observation were computed.

In [25]:
df.gauge_name.value_counts()

Rio Aconcagua En Chacabuquito                   14638
Rio Cruces En Rucaco                            14617
Rio Choapa En Cuncumen                          14607
Rio Elqui En Algarrobal                         14602
Rio Cautin En Cajon                             14571
                                                ...  
Estero Chimbarongo En Santa Cruz                  328
Rio Chillan En Longitudinal                       302
Rio Pama Entrada Embalse Cogoti                   195
Estero Las Vegas Aguas Abajo Canal Las Vegas      195
Rio Blanco En Chaiten                             175
Name: gauge_name, Length: 503, dtype: int64

Some stations contains much more observations than others. Let's verify its distribution on Chile map considering the location through latitude and longitude.

### mean_elev

mean_elev represents mean altitude of the watershed. So, it directly influences other variables, like temperature, for example. So, let's analyse it and turn it into a categorical variable through intervals.

In [26]:
df['mean_elev'].describe()

count    4.175037e+06
mean     1.760149e+03
std      1.382302e+03
min      1.181229e+02
25%      5.847012e+02
50%      1.195311e+03
75%      3.048161e+03
max      4.910152e+03
Name: mean_elev, dtype: float64

We can see that the minimum value of this variable is 118.12 and maximum is 4910. So the watersheds on the database are located in very different altitudes. In order to make this information usefull, we will turn it into a categorical variable.

In [27]:
mean_elev_bar = pd.cut(df['mean_elev'], bins=20).value_counts(sort = False).reset_index()
mean_elev_bar.rename(columns={'index':'interval','mean_elev':'number_of_observations_elev_interval'}, inplace=True)

In [28]:
mean_elev_bar['interval'] = mean_elev_bar['interval'].astype(str)

In [29]:
alt.Chart(mean_elev_bar).mark_bar().encode(
    x=alt.X('interval', bin='binned', sort=None),
    y='number_of_observations_elev_interval'
)

alt.Chart(...)

The majority of the observations in the database came from watersheds located in lower places.

In [30]:
df['mean_elev_categorical'] = pd.cut(df['mean_elev'], bins=20, labels=range(20))

In [31]:
df.head()

date  basin_id   flux  precip   temp_max                 gauge_name  \
0 1980-01-01   1001001  0.579     0.0  10.685653  Rio Caquena En Nacimiento   
1 1980-01-02   1001001  0.543     0.0  11.470960  Rio Caquena En Nacimiento   
2 1980-01-03   1001001  0.482     0.0  11.947457  Rio Caquena En Nacimiento   
3 1980-01-04   1001001  0.459     0.0  12.424489  Rio Caquena En Nacimiento   
4 1980-01-05   1001001  0.436     0.0  12.649203  Rio Caquena En Nacimiento   

       lat      lon    mean_elev   area_km2 mean_elev_categorical  
0 -18.0769 -69.1961  4842.449328  49.711859                    19  
1 -18.0769 -69.1961  4842.449328  49.711859                    19  
2 -18.0769 -69.1961  4842.449328  49.711859                    19  
3 -18.0769 -69.1961  4842.449328  49.711859                    19  
4 -18.0769 -69.1961  4842.449328  49.711859                    19

### area_km2

The area of the watershed may influence the flux into a watershed, because the larger the area, the larger the drainage area of the watershed. And the drainage area is directly responsible for capturing the precipitation water. So let's analyse this variable as we made with mean_elev.

In [32]:
df.area_km2.describe()

count    4.175037e+06
mean     2.403915e+03
std      4.321229e+03
min      1.789123e+01
25%      3.761001e+02
50%      8.205541e+02
75%      2.461610e+03
max      5.224367e+04
Name: area_km2, dtype: float64

We can see that the minimum value of this variable is 17.89 and maximum is 52243.6. So the watersheds on the database contains very different sizes. In order to make this information usefull, we will turn it into a categorical variable.

In [33]:
mean_area_km2 = pd.cut(df['area_km2'], bins=50).value_counts(sort = False).reset_index()
mean_area_km2.rename(columns={'index':'interval','area_km2':'number_of_observations_area_interval'}, inplace=True)

In [34]:
mean_area_km2['interval'] = mean_area_km2['interval'].astype(str)

In [35]:
alt.Chart(mean_area_km2).mark_bar().encode(
    x=alt.X('interval', bin='binned', sort=None),
    y='number_of_observations_area_interval'
)

alt.Chart(...)

The majority of the observations in the database came from watersheds with area smaller than 1062 km2.

In [36]:
df['area_km2_categorical'] = pd.cut(df['area_km2'], bins=50, labels=range(50))

In [37]:
df.head()

date  basin_id   flux  precip   temp_max                 gauge_name  \
0 1980-01-01   1001001  0.579     0.0  10.685653  Rio Caquena En Nacimiento   
1 1980-01-02   1001001  0.543     0.0  11.470960  Rio Caquena En Nacimiento   
2 1980-01-03   1001001  0.482     0.0  11.947457  Rio Caquena En Nacimiento   
3 1980-01-04   1001001  0.459     0.0  12.424489  Rio Caquena En Nacimiento   
4 1980-01-05   1001001  0.436     0.0  12.649203  Rio Caquena En Nacimiento   

       lat      lon    mean_elev   area_km2 mean_elev_categorical  \
0 -18.0769 -69.1961  4842.449328  49.711859                    19   
1 -18.0769 -69.1961  4842.449328  49.711859                    19   
2 -18.0769 -69.1961  4842.449328  49.711859                    19   
3 -18.0769 -69.1961  4842.449328  49.711859                    19   
4 -18.0769 -69.1961  4842.449328  49.711859                    19   

  area_km2_categorical  
0                    0  
1                    0  
2                    0  
3                    0  
4                    0

### Season

Finnally, considering the season influences directly the temperature, let's create a new column on our database containing the season in Chile on date of the observation. The season there are as follows:
- Summer: from December to February
- Autumn: from March to May
- Winter: from June to August
- Spring: from September to November

In [38]:
map_season = {1:'Summer', 2: 'Summer', 3: 'Autumn', 4: 'Autumn', 5: 'Autumn', 6: 'Winter', 7: 'Winter', 8: 'Winter', 9: 'Spring', 10: 'Spring', 11: 'Spring', 12: 'Summer'}

In [39]:
df['season'] = df.date.dt.month.map(map_season)

In [40]:
df.season.value_counts()

Autumn    1056597
Summer    1041105
Winter    1039615
Spring    1037720
Name: season, dtype: int64

## 3. Plot flux, temperature and precipitations:

### a) Write a function that plot a time series of a specific variable (flux, temp, precip) from a station.

In [41]:
def plot_one_timeserie(cod_station, variable, min_date, max_date):
    df_station = df[(df.basin_id==cod_station)&(df.date.between(left=min_date, right=max_date, inclusive='both'))]
    
    line = alt.Chart(df_station).mark_line().encode(
        x=alt.X("date"),
        y=alt.Y(f'{variable}')
    ).properties(width=800, height=300)
    
    return line

In [42]:
plot_one_timeserie(cod_station=12930001, variable='flux', min_date='2019-01-01', max_date='2020-01-10')

alt.Chart(...)

In [43]:
plot_one_timeserie(cod_station=12930001, variable='temp_max', min_date='2019-01-01', max_date='2020-01-10')

alt.Chart(...)

In [44]:
plot_one_timeserie(cod_station=12930001, variable='precip', min_date='2019-01-01', max_date='2020-01-10')

alt.Chart(...)

### b) Now write a function that plots the 3 variables at the same time. As the variables are in different scales, you can normalize before plotting them.

In [45]:
def plot_three_timeseries(cod_station, min_date, max_date):
    df_station = df[(df.basin_id==cod_station)&(df.date.between(left=min_date, right=max_date, inclusive='both'))].copy()
    
    df_station['flux'] = (df_station['flux'] - df_station['flux'].min()) / (df_station['flux'].max() - df_station['flux'].min())
    df_station['temp_max'] = (df_station['temp_max'] - df_station['temp_max'].min()) / (df_station['temp_max'].max() - df_station['temp_max'].min())
    df_station['precip'] = (df_station['precip'] - df_station['precip'].min()) / (df_station['precip'].max() - df_station['precip'].min())

    
    lines = alt.Chart(df_station).mark_line().transform_fold(
        fold=['flux','temp_max', 'precip'], 
        as_=['variable', 'value']
    ).encode(
        x='date:T',
        y='value:Q',
        color='variable:N'
    ).properties(width=800, height=300)
    
    return lines

In [46]:
plot_three_timeseries(12930001,min_date='2019-01-01', max_date='2020-01-10')

alt.Chart(...)

## 4. Create three variables called:

- flux_extreme
- temp_extreme
- precip_extreme

I will consider the season variable created above to detect extreme events depending on what does it mean to be extreme in each season. Then, I must calculate the 95 percentile depending on the season.

In [47]:
percentiles_95 = df.groupby('season')[['flux', 'temp_max', 'precip']].quantile(0.95)

In [48]:
percentiles_95

flux   temp_max     precip
season                             
Autumn  170.0  24.159966  18.092802
Spring  310.0  22.571383  13.672440
Summer  185.0  28.260483   7.404016
Winter  407.0  16.085831  30.503264

### flux_extreme

In [ ]:
# df['flux_extreme'] = np.where(df.flux>df.flux.quantile(0.95), 1, 0)

In [51]:
df['flux_extreme'] = 0
for season in ['Autumn','Spring','Summer','Winter']:
    df.loc[(df.season==season)&(df.flux>percentiles_95.loc[season,'flux']),'flux_extreme'] = 1

In [52]:
df.flux_extreme.value_counts()

0    3966752
1     208285
Name: flux_extreme, dtype: int64

In [60]:
df.groupby('season').flux_extreme.value_counts()

season  flux_extreme
Autumn  0               1003927
        1                 52670
Spring  0                985917
        1                 51803
Summer  0                989180
        1                 51925
Winter  0                987728
        1                 51887
Name: flux_extreme, dtype: int64

### temp_extreme

In [57]:
df['temp_extreme'] = 0
for season in ['Autumn','Spring','Summer','Winter']:
    df.loc[(df.season==season)&(df.temp_max>percentiles_95.loc[season,'temp_max']),'temp_extreme'] = 1

In [58]:
df['temp_extreme'].value_counts()

0    3966284
1     208753
Name: temp_extreme, dtype: int64

In [61]:
df.groupby('season').temp_extreme.value_counts()

season  temp_extreme
Autumn  0               1003767
        1                 52830
Spring  0                985834
        1                 51886
Summer  0                989049
        1                 52056
Winter  0                987634
        1                 51981
Name: temp_extreme, dtype: int64

### precip_extreme

In [67]:
df['precip_extreme'] = 0
for season in ['Autumn','Spring','Summer','Winter']:
    df.loc[(df.season==season)&(df.precip>percentiles_95.loc[season,'precip']),'precip_extreme'] = 1

In [68]:
df['precip_extreme'].value_counts()

0    3966284
1     208753
Name: precip_extreme, dtype: int64

In [69]:
df.groupby('season').precip_extreme.value_counts()

season  precip_extreme
Autumn  0                 1003767
        1                   52830
Spring  0                  985834
        1                   51886
Summer  0                  989049
        1                   52056
Winter  0                  987634
        1                   51981
Name: precip_extreme, dtype: int64

In [74]:
df[(df['temp_extreme']==1)&(df['flux_extreme']==1)&(df['precip_extreme']==1)]

date  basin_id    flux     precip   temp_max  \
2133678 1982-06-05   7357002   718.0  35.302013  17.163368   
2159720 1982-06-05   7359001  1207.0  40.891627  16.886510   

                           gauge_name      lat      lon   mean_elev  \
2133678      Rio Loncomilla En Bodega -35.8167 -71.8333  398.357548   
2159720  Rio Loncomilla En Las Brisas -35.6169 -71.7678  489.063443   

            area_km2 mean_elev_categorical area_km2_categorical  season  \
2133678  7078.839578                     1                    6  Winter   
2159720  9923.684597                     1                    9  Winter   

         flux_extreme  temp_extreme  precip_extreme  
2133678             1             1               1  
2159720             1             1               1

## 5. Plot the variable flux_extreme. Are there any different behaviours among different watersheds?

In [109]:
alt.Chart(df.groupby('gauge_name').flux_extreme.sum().reset_index()).mark_bar().encode(
    x=alt.X('gauge_name'),
    y='flux_extreme'
)

alt.Chart(...)

In [105]:
df_extreme_per_watershed = df.set_index('date').groupby('gauge_name').resample('3M').flux_extreme.sum().reset_index()
alt.Chart(df_extreme_per_watershed).mark_line().encode(
    x=alt.X("date"),
    y=alt.Y('flux_extreme'),
    color='gauge_name',
    #row="gauge_name:N"
).properties(width=800, height=300)

alt.Chart(...)

From the graphs above, we can see that there are some basins where extreme flows are much more frequent than in the others. Some of them didn't even have an extreme flow throughout the period.

## 6. Plot the percentage of extreme events during time. Have they become more frequent?

In [95]:
df_extreme_overtime = df.set_index('date').resample('3M')[['flux_extreme','temp_extreme','precip_extreme']].mean().reset_index()

alt.Chart(df_extreme_overtime).mark_line().transform_fold(
        fold=['flux_extreme','temp_extreme', 'precip_extreme'], 
        as_=['variable', 'value']
    ).encode(
        x='date:T',
        y=alt.Y('value:Q'),
        color='variable:N',
        row="variable:N"
    ).properties(width=800, height=300)


alt.Chart(...)

Considering the percentage of extreme events per quarter:
- flux extreme seems to become more frequent after 2002
- precipitation seems to become less frequent, considering that in no quarter after 2008 did it occur in more than 10% of the observations
- temperature seems to keep the same seasonal frequency

## 7. Extreme flux prediction

For flux prediction, I chose to use XGBoost model. The reason for that is that it is a simple binary classification problem with only numeric and categorical variables.
Then, I will consider variables temp_extreme, precip_extreme, area_km2_categorical, mean_elev_categorical and season_categorical

Considering that flux_extreme is an imbalanced class, I will set the parameter scale_pos_weight to 5, so I will impose greater penalties for errors on the minor class, in this case any incidentes of 1 in the response variable, i.e., flux extreme. I chose to use this type of penalty because the imbalance is important for that case, as extreme events are actually rarer. So I chose to keep it rarer instead of trying to make both classes equal (0 and 1 for extreme flux) and penalize the chose to the bigger class, so I will avoid that the model just choose everything as "no extreme". 

In [113]:
df['season_categorical'] = df.season.map({'Summer':1, 'Autumn':2, 'Winter': 3, 'Spring': 4}).astype('category')

In [152]:
df['season_categorical'] = df['season_categorical'].cat.codes
df['area_km2_categorical'] = df['area_km2_categorical'].cat.codes
df['mean_elev_categorical'] = df['mean_elev_categorical'].cat.codes

In [214]:
# split data into X and y
X = df.loc[:,['temp_extreme', 'precip_extreme','season_categorical', 'area_km2_categorical', 'mean_elev_categorical']]
Y = df.loc[:,'flux_extreme']

In [215]:
# split data into train and test sets
seed = 7
test_size = 0.33
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=test_size, random_state=seed)

In [216]:
# fit model no training data
model = XGBClassifier(learning_rate=0.001,
                      max_depth = 1,
                      n_estimators = 100,
                      scale_pos_weight=5)
model.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.001, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=1, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=0, num_parallel_tree=1, predictor='auto', random_state=0,
              reg_alpha=0, reg_lambda=1, ...)

In [217]:
# make predictions for test data
y_pred = model.predict(X_test)
predictions = [round(value) for value in y_pred]

In [218]:
# evaluate predictions
print(classification_report(y_test,predictions))

              precision    recall  f1-score   support

           0       0.99      0.87      0.93   1308770
           1       0.25      0.83      0.38     68993

    accuracy                           0.87   1377763
   macro avg       0.62      0.85      0.65   1377763
weighted avg       0.95      0.87      0.90   1377763



### Analyze the model results.

For this case of extreme flux prediction, it is better to think about optimize the **recall** because I must minimize false negatives - it is bad to predict that there will not be an extreme flow when, in fact, it will. So, recall gave us a good number considering the penalty we applied.

On the other hand, from precision, we can notice that the model is classifing many false positives. Maybe our penalty is too high. So, let's consider a smaller penalty calibrating scale_pos_weight and see whats hapens.

#### scale_pos_weight = 3

In [219]:
model3 = XGBClassifier(learning_rate=0.001,
                      max_depth = 1,
                      n_estimators = 100,
                      scale_pos_weight=3)
model3.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.001, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=1, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=0, num_parallel_tree=1, predictor='auto', random_state=0,
              reg_alpha=0, reg_lambda=1, ...)

In [220]:
# make predictions for test data
y_pred3 = model3.predict(X_test)
predictions3 = [round(value) for value in y_pred3]

In [221]:
# evaluate predictions
print(classification_report(y_test,predictions3))

              precision    recall  f1-score   support

           0       0.98      0.93      0.95   1308770
           1       0.33      0.67      0.44     68993

    accuracy                           0.91   1377763
   macro avg       0.65      0.80      0.70   1377763
weighted avg       0.95      0.91      0.93   1377763



#### scale_pos_weight = 4

In [222]:
model4 = XGBClassifier(learning_rate=0.001,
                      max_depth = 1,
                      n_estimators = 100,
                      scale_pos_weight=4)
model4.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.001, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=1, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=0, num_parallel_tree=1, predictor='auto', random_state=0,
              reg_alpha=0, reg_lambda=1, ...)

In [223]:
# make predictions for test data
y_pred4 = model4.predict(X_test)
predictions4 = [round(value) for value in y_pred4]

In [224]:
# evaluate predictions
print(classification_report(y_test,predictions4))

              precision    recall  f1-score   support

           0       0.99      0.87      0.93   1308770
           1       0.25      0.83      0.38     68993

    accuracy                           0.87   1377763
   macro avg       0.62      0.85      0.65   1377763
weighted avg       0.95      0.87      0.90   1377763



With scale_pos_weight as 3, the precision increased a little, but recall was considerably smaller. So, it's better to keep the penalty higher, at least 4.